# ML Trader

In [1]:
from utils.packages import *
from utils.variables import *
from utils.i_o import *
from utils.dir_slope import *
from utils.engine import *
from utils.loops import *
from utils.order import *
import winsound

In [2]:
def get_tick_time(data):
    data['df']['sno'] = data['df'].index
    data['df']['tick']      = (data["df"]['Ask'] + data["df"]['Bid'])/2
    data['df']['DateTime_frmt']   = [dt.datetime.strptime(x.split(".")[0],"%Y%m%d %H:%M:%S") for x in data["df"]['DateTime']]
    return(data)

In [3]:
def get_ohlc(data):
    
    data['df_bars']['sno'] = data['df'].resample(data['candle_size'], on='DateTime_frmt').sno.first().values.astype(int)
    data['df_bars']['o'] = data['df'].resample(data['candle_size'], on='DateTime_frmt').tick.first().values
    data['df_bars']['h'] = data['df'].resample(data['candle_size'], on='DateTime_frmt').tick.max().values
    data['df_bars']['l'] = data['df'].resample(data['candle_size'], on='DateTime_frmt').tick.min().values
    data['df_bars']['c'] = data['df'].resample(data['candle_size'], on='DateTime_frmt').tick.last().values
    data['df_bars'] = data['df_bars'].reset_index(drop=True)    
    return(data)

In [4]:
def get_sup_res(data):
    if data['fractal_one_side_bar_count'] == 2:
        for i in range(2, len(data['df_bars'])):
            if 1 < i < len(data['df_bars']) - 2:
                if data['df_bars']['l'][i] < data['df_bars']['l'][i-1] < data['df_bars']['l'][i-2] and data['df_bars']['l'][i] < data['df_bars']['l'][i+1] < data['df_bars']['l'][i+2]:
                    data['df_bars']['support'][i] = 'yes'

                if data['df_bars']['h'][i] > data['df_bars']['h'][i-1] > data['df_bars']['h'][i-2] and data['df_bars']['h'][i] > data['df_bars']['h'][i+1] > data['df_bars']['h'][i+2]:
                    data['df_bars']['resistance'][i] = 'yes'

    if data['fractal_one_side_bar_count'] == 1:
        for i in range(1, len(data['df_bars'])):
            if 1 < i < len(data['df_bars']) - 1:
                if data['df_bars']['l'][i] < data['df_bars']['l'][i-1] and data['df_bars']['l'][i] < data['df_bars']['l'][i+1]:
                    data['df_bars']['support'][i] = 'yes'

                if data['df_bars']['h'][i] > data['df_bars']['h'][i-1] and data['df_bars']['h'][i] > data['df_bars']['h'][i+1]:
                    data['df_bars']['resistance'][i] = 'yes'

    return(data)

In [5]:
def combine_nearby_lines(data): 

    data['df'] = pd.merge(data['df'], data['df_bars'], on = 'sno', how = 'left')
    
#     data['sup_res_last_window_df'] = data['df'][-data['sup_res_data_last_ticks_window']:]
#     data['support_values'] = list(data['sup_res_last_window_df']['l'][data['sup_res_last_window_df']['support'] == 'yes'])
#     data['resistance_values'] = list(data['sup_res_last_window_df']['h'][data['sup_res_last_window_df']['resistance'] == 'yes'])

    data['support_values'] = list(data['df']['l'][data['df']['support'] == 'yes'])
    data['resistance_values'] = list(data['df']['h'][data['df']['resistance'] == 'yes'])
    
    data['combined_sup_res'] = list(np.round(data['support_values'] + data['resistance_values'],4))    
    
    check_list = ['No'] * len(data['combined_sup_res'])
    data['dup_removed_sup_res'] = {}
    cntr = 1
    actual_position = 0

    for i in range(len(data['combined_sup_res'])):   
        if check_list[i] == 'No':
            cntr = 1
            check_list[i] =  'Done'

            for j in range(i+1,len(data['combined_sup_res'])):
                if np.abs(data['combined_sup_res'][i] - data['combined_sup_res'][j]) < 0.0002:
                    cntr = cntr + 1
                    check_list[j] = 'Done'
                    #print(i,j, data['combined_sup_res'][i], data['combined_sup_res'][j], np.abs(data['combined_sup_res'][i] - data['combined_sup_res'][j]), cntr, check_list[j])

            actual_position  = actual_position + cntr
            data['dup_removed_sup_res'][data['combined_sup_res'][i]] = cntr

    data['dup_removed_sup_res'] = [k for k in data['dup_removed_sup_res'] if data['dup_removed_sup_res'][k] >= data['sup_res_touches']]        
    
    return(data)

%%time
data['df'] = pd.read_csv('data/EURUSD_2021.csv', nrows=5000)

In [6]:
data['df_bars'] = pd.DataFrame()
data['df_bars']['support'] = ''
data['df_bars']['resistance'] = ''
data['candle_size'] = '5T'
data['fractal_one_side_bar_count'] = 1
data['sup_res_touches'] = 2
data['sup_res_last_ticks_window'] = 10_000

In [7]:
data = get_date_list(data)
data = read_data(data)

Record num : 10000


In [8]:
data = get_tick_time(data)
data = get_ohlc(data)
data = get_sup_res(data)
data = combine_nearby_lines(data)
data = get_rolling_emas(data)

0it [00:00, ?it/s]

Building Lema...


8401it [00:06, 1298.17it/s]
139it [00:00, 1270.47it/s]

Building SLema...


8001it [00:05, 1335.29it/s]
113it [00:00, 1094.29it/s]

Building Sema...


7921it [00:05, 1321.26it/s]


In [9]:
data['df']['long_open'] = ''
data['df']['long_close'] = ''
data['df']['short_open'] = ''
data['df']['short_close'] = ''

In [10]:
for data['i'] in tqdm(range(0, data['df_len'])):

    data['bid'] = data["df"]['Bid'][data['i']]        
    data['ask'] = data["df"]['Ask'][data['i']]
    data['tick'] = data['df']['tick'][data['i']]        
    data['dt_val'] = data['df']['DateTime_frmt'][data['i']]   
    data['sema'] = data['df']['sema'][data['i']]      
    data['slema'] = data['df']['slema'][data['i']]      
    data['lema'] = data['df']['lema'][data['i']]    

    data = get_position(data)

    # Get Dirs --------------------------------
    if len(data['dir_list']) < 2:
        data['dir_list'].append(data['position'])   
        continue

    elif len(data['dir_list']) == 2:
        data = get_cross_dir(data)
    # ----------------------------------------------------------  

    data = calculate_pl(data)
    data = simple_stop_loss(data)
    data = simple_take_profit(data)   
    data = make_order(data)          

100%|████████████████████████████████████| 7920/7920 [00:00<00:00, 9035.69it/s]

pls   -0.00101
dtype: float64
--------------------------------------
                  date ord_types          close_type      pls
0  2021-01-03 23:18:09     short         simple_stop -0.00020
1  2021-01-03 23:29:24      long  simple_take_profit  0.00020
2  2021-01-04 00:01:10     short         simple_stop -0.00020
3  2021-01-04 00:01:45      long         simple_stop -0.00021
4  2021-01-04 00:13:55      long         simple_stop -0.00020
5  2021-01-04 00:16:38     short  simple_take_profit  0.00020
6  2021-01-04 00:30:34      long         simple_stop -0.00020
7  2021-01-04 00:36:59     short  simple_take_profit  0.00020
8  2021-01-04 00:48:26      long         simple_stop -0.00020
9  2021-01-04 00:52:21     short         simple_stop -0.00020
10 2021-01-04 01:05:07     short         simple_stop -0.00020


In [29]:
fig = px.line(data['df'], 
              x="DateTime_frmt", 
              y=['tick', 'sema','slema', 'lema'], 
              color_discrete_sequence = ['grey', 'red', 'blue', 'black'],
              title='tick chart') 

data['marker_size'] = 15

fig.add_scatter(x = data['df']['DateTime_frmt'] , 
                y = data['df']['long_open'], 
                mode = 'markers', 
                name = 'long_open',
                marker_symbol = 'triangle-up',
                marker=dict(color='lightgreen',
                            size=data['marker_size'],
                            line=dict(
                                color='green',
                                width=2
                            )),
                opacity=1)


fig.add_scatter(x = data['df']['DateTime_frmt'] , 
                y = data['df']['long_close'], 
                mode = 'markers', 
                name = 'long_close',
                marker_symbol = 'triangle-up',
                marker=dict(color='red',
                            size=data['marker_size'],
                            line=dict(
                                color='darkred',
                                width=2
                            )),
                opacity=1)


fig.add_scatter(x = data['df']['DateTime_frmt'] , 
                y = data['df']['short_open'], 
                mode = 'markers', 
                name = 'short_open',
                marker_symbol = 'triangle-down',
                marker=dict(color='lightgreen',
                            size=data['marker_size'],
                            line=dict(
                                color='green',
                                width=2
                            )),
                opacity=1)


fig.add_scatter(x = data['df']['DateTime_frmt'] , 
                y = data['df']['short_close'], 
                mode = 'markers', 
                name = 'short_close',
                marker_symbol = 'triangle-down',
                marker=dict(color='red',
                            size=data['marker_size'],
                            line=dict(
                                color='darkred',
                                width=2
                            )),
                opacity=1)


for val in data['dup_removed_sup_res']:
    fig.add_hline(y = val, line_width=0.5, line_dash="dot", line_color="darkred")  

# fig.update_layout(paper_bgcolor="white", plot_bgcolor="white")
    
fig.show()